problemas:

- que modelo usar para Sentiment Analysis ?


tentar NER + Sentiment Analysis

---

to do now:

- ~~save all data in a single column or something different inside the parquet~~

- ~~add news source to dicionary~~

- ~~convert timestamp to YYYYMM because ts is from archived, not the new itself~~

- ~~reorder dicionary~~

In [100]:
import pandas as pd
from datetime import datetime

---

**merged api columns into news**

In [101]:
df = pd.read_parquet("data03.parquet").map(lambda x: list(x))
df['news'] = df.iloc[:, 1:].sum(axis=1)
df_filtered = df.iloc[:, [0, -1]]
df_filtered

aliases  \
companies                                                                      
Banco Comercial Português                   [Banco Comercial Português, BCP]   
Galp Energia                                            [Galp Energia, GALP]   
EDP                        [EDP, Energias de Portugal, Electricidade de P...   
Sonae                                                           [Sonae, SON]   
Mota-Engil                                                 [Mota-Engil, EGL]   

                                                                        news  
companies                                                                     
Banco Comercial Português  [{'ExtractedText': 'DN   13 de Setembro de 200...  
Galp Energia               [{'ExtractedText': 'RTP Galp reforça posição n...  
EDP                        [{'ExtractedText': 'DN-Sinteses Negocios 9 de ...  
Sonae                      [{'ExtractedText': 'DN-Sinteses 5 de Março de ...  
Mota-Engil                 [{'ExtractedText': 'RTP Lucro da Mota-Engil so...

In [102]:
df_filtered.map(len)

aliases  news
companies                               
Banco Comercial Português        2  1284
Galp Energia                     2  1338
EDP                              3  1456
Sonae                            2   899
Mota-Engil                       2   459

**convert timestamp +  add sources + reorder dictionary**

In [103]:
def tstampANDsourceANDreorderdict(lista):
    new_list = []
    noticias = pd.read_csv("noticias.csv")
    for req in lista:
        # news source
        linkToArchive = req["linkToArchive"]
        foundSource = False
        for index, row in noticias.iterrows():
            if row.iloc[0] in linkToArchive:
                req["newsSource"] = row.iloc[1]
                foundSource = True
                break
            else:
                pass
        if not foundSource:
            req["newsSource"] = "unknown"
        # timestamp
        req["tstamp"] = req["tstamp"][:6]
        # reorder dict
        ordered_keys = ["tstamp", "newsSource", "newsProbability", "linkToArchive", "ExtractedText"]
        reordered_dict = {key: req[key] for key in ordered_keys}
        # SAVE
        new_list.append(reordered_dict)
    return new_list

df_filtered.loc[:, "news"] = df_filtered["news"].map(lambda x: tstampANDsourceANDreorderdict(x))

In [104]:
df_filtered.iloc[0,-1][0]

{'tstamp': '200109',
 'newsSource': 'Diário de Notícias',
 'newsProbability': 0.933,
 'linkToArchive': 'https://arquivo.pt/wayback/20010913052557/http://www.dn.pt/int/13p4x.htm',
 'ExtractedText': 'DN \xa0 13 de Setembro de 2001 Intalações do BCP servem de refúgio As instalações do Banco Comercial Português, em Wall Street, foram utilizadas como refúgio por dezenas de pessoas depois dos atentados ao World Trade Center. Nenhum dos 48 funcionários daquela sucursal bancário ficou ferido e os dois trabalhadores que ainda não tinham comunicado com empresa fizeram-no na madrugada de ontem. Voo TAP para Newark chega hoje O voo 1331 da TAP que partiu terça-feira de Lisboa para Newark, nos Estados Unidos, deve chegar hoje ao seu destino. Segundo anunciou a porta-voz da companhia aérea, o avião foi direccionado para a cidade de Halifax, no Canadá, quando os EUA encerraram todos os seus aeroportos a vôos comerciais que se dirigissem para o território. EUA agradecem apoio português O representante

---

In [106]:
df_filtered.map(len)

aliases  news
companies                               
Banco Comercial Português        2  1284
Galp Energia                     2  1338
EDP                              3  1456
Sonae                            2   899
Mota-Engil                       2   459

In [107]:
from fuzzywuzzy import fuzz
import random

def nearDuplicates(lista, threshold=90):
    total_data = len(lista) # status
    curr_data = 0 # status
    new_list = [lista[0]]
    texts = [lista[0]["ExtractedText"]]
    for req in lista[1:]:
        curr_data += 1 # status
        ExtractedText = req["ExtractedText"]
        similarity = 0
        for txt in texts:
            similarity = max(similarity, fuzz.ratio(txt, ExtractedText))
            if similarity > threshold:
                break
        if similarity <= threshold:
            new_list.append(req)
            texts.append(ExtractedText)
        if random.uniform(0, 1) < 0.01: # status
            print(f"{curr_data} of {total_data}", end = " | ") # status
    print("") # status
    return new_list

df_filtered.loc[:, "news"] = df_filtered["news"].map(lambda x: nearDuplicates(x))
df_filtered.map(len)

42 of 1284 | 309 of 1284 | 348 of 1284 | 799 of 1284 | 936 of 1284 | 1027 of 1284 | 1145 of 1284 | 1226 of 1284 | 
267 of 1338 | 315 of 1338 | 323 of 1338 | 339 of 1338 | 380 of 1338 | 386 of 1338 | 389 of 1338 | 412 of 1338 | 510 of 1338 | 570 of 1338 | 615 of 1338 | 764 of 1338 | 917 of 1338 | 950 of 1338 | 977 of 1338 | 1058 of 1338 | 1062 of 1338 | 1073 of 1338 | 1206 of 1338 | 
51 of 1456 | 76 of 1456 | 526 of 1456 | 660 of 1456 | 678 of 1456 | 689 of 1456 | 885 of 1456 | 993 of 1456 | 1203 of 1456 | 
209 of 899 | 285 of 899 | 598 of 899 | 623 of 899 | 715 of 899 | 734 of 899 | 758 of 899 | 779 of 899 | 873 of 899 | 890 of 899 | 
37 of 459 | 38 of 459 | 40 of 459 | 261 of 459 | 284 of 459 | 313 of 459 | 389 of 459 | 


aliases  news
companies                               
Banco Comercial Português        2   807
Galp Energia                     2   809
EDP                              3   954
Sonae                            2   520
Mota-Engil                       2   296

In [108]:
df_filtered.iloc[0,1] # 677 658 814 434 249

[{'tstamp': '200109',
  'newsSource': 'Diário de Notícias',
  'newsProbability': 0.933,
  'linkToArchive': 'https://arquivo.pt/wayback/20010913052557/http://www.dn.pt/int/13p4x.htm',
  'ExtractedText': 'DN \xa0 13 de Setembro de 2001 Intalações do BCP servem de refúgio As instalações do Banco Comercial Português, em Wall Street, foram utilizadas como refúgio por dezenas de pessoas depois dos atentados ao World Trade Center. Nenhum dos 48 funcionários daquela sucursal bancário ficou ferido e os dois trabalhadores que ainda não tinham comunicado com empresa fizeram-no na madrugada de ontem. Voo TAP para Newark chega hoje O voo 1331 da TAP que partiu terça-feira de Lisboa para Newark, nos Estados Unidos, deve chegar hoje ao seu destino. Segundo anunciou a porta-voz da companhia aérea, o avião foi direccionado para a cidade de Halifax, no Canadá, quando os EUA encerraram todos os seus aeroportos a vôos comerciais que se dirigissem para o território. EUA agradecem apoio português O represen

In [110]:
#df_filtered.to_parquet("data04.parquet")

In [111]:
pd.read_parquet("data04.parquet")

aliases  \
companies                                                                      
Banco Comercial Português                   [Banco Comercial Português, BCP]   
Galp Energia                                            [Galp Energia, GALP]   
EDP                        [EDP, Energias de Portugal, Electricidade de P...   
Sonae                                                           [Sonae, SON]   
Mota-Engil                                                 [Mota-Engil, EGL]   

                                                                        news  
companies                                                                     
Banco Comercial Português  [{'ExtractedText': 'DN   13 de Setembro de 200...  
Galp Energia               [{'ExtractedText': 'RTP Galp reforça posição n...  
EDP                        [{'ExtractedText': 'DN-Sinteses Negocios 9 de ...  
Sonae                      [{'ExtractedText': 'DN-Sinteses 5 de Março de ...  
Mota-Engil                 [{'ExtractedText': 'RTP Lucro da Mota-Engil so...